# 2)A)train  a  decision  tree  classification  model  using  information  gain  as  the  splitting  criterion  

In [22]:
import numpy as np
import pandas as pd
import math


In [23]:
from collections import OrderedDict

data_types = OrderedDict([
    ("age", "int"),
    ("workclass", "category"),
    ("final_weight", "int"),
    ("education", "category"),
    ("education_num", "int"),
    ("marital_status", "category"),
    ("occupation", "category"),
    ("relationship", "category"),
    ("race", "category"),
    ("sex", "category"),
    ("capital_gain", "float"),
    ("capital_loss", "int"),
    ("hours_per_week", "int"),
    ("native_country", "category"),
    ("income_class", "category"),
])
predict = "income_class"

DataCleaning

In [24]:
def cleaning(data):
    data['income_class'] = data.income_class.str.rstrip('.').astype('category')
    data = data.drop('final_weight', axis=1)
    data = data.drop_duplicates()
    data[predict] = (data[predict] == '>50K').astype('int')
    return data

In [25]:
def dataset(path):
    return pd.read_csv(
        path,
        names=data_types,
        index_col=None,
        comment='|',
        skipinitialspace=True,
        na_values={'capital_gain': 99999,'workclass': '?','native_country': '?','occupation': '?'},
        dtype=data_types,
    )


In [26]:
train_data = cleaning(dataset(r'C:\Users\Amar Raja\Desktop\iitkML\assignment1\DT\adult.data'))
test_data = cleaning(dataset(r'C:\Users\Amar Raja\Desktop\iitkML\assignment1\DT\adult.test'))

In [27]:
df = pd.concat([train_data,test_data])
df.dtypes

age                  int32
workclass         category
education         category
education_num        int32
marital_status    category
occupation        category
relationship      category
race              category
sex               category
capital_gain       float64
capital_loss         int32
hours_per_week       int32
native_country      object
income_class         int32
dtype: object

In [28]:
df = pd.concat([train_data, test_data])
df["workclass"] = df["workclass"].cat.codes
df["education"] = df["education"].cat.codes
df["marital_status"] = df["marital_status"].cat.codes
df["occupation"] = df["occupation"].cat.codes
df["relationship"] = df["relationship"].cat.codes
df["race"] = df["race"].cat.codes
df["sex"] = df["sex"].cat.codes
df['native_country'] = df.native_country.astype('category')
df["native_country"] = df["native_country"].cat.codes
df = df.drop(['capital_loss', 'capital_gain'], axis=1)
df.head()

age  workclass  education  education_num  marital_status  occupation  \
0   39          6          9             13               4           0   
1   50          5          9             13               2           3   
2   38          3         11              9               0           5   
3   53          3          1              7               2           5   
4   28          3          9             13               2           9   

   relationship  race  sex  hours_per_week  native_country  income_class  
0             1     4    1              40              38             0  
1             0     4    1              13              38             0  
2             1     4    1              40              38             0  
3             0     2    1              40              38             0  
4             5     2    0              40               4             0

In [29]:
bins = [0, 20, 30, 40, 50, 60, np.inf]
names = ['0', '1', '2', '3', '4', '5']

df['age'] = pd.cut(df['age'], bins, labels=names)
df["age"] = df["age"].astype('category').cat.codes

bins = [0, 3, 6, 9, 12, 15, np.inf]
names = ['0', '1', '2', '3', '4', '5']

df['education_num'] = pd.cut(df['education_num'], bins, labels=names)
df["education_num"] = df["education_num"].astype('category').cat.codes

bins = [0, 15, 30, 45, 60, 75, np.inf]
names = ['0', '1', '2', '3', '4', '5']

df['hours_per_week'] = pd.cut(df['hours_per_week'], bins, labels=names)
df["hours_per_week"] = df["hours_per_week"].astype('category').cat.codes

df.dtypes

age                int8
workclass          int8
education          int8
education_num      int8
marital_status     int8
occupation         int8
relationship       int8
race               int8
sex                int8
hours_per_week     int8
native_country     int8
income_class      int32
dtype: object

In [30]:
class TreeNode:
    def __init__(self, data, output):
        self.data = data
        self.children = {}
        self.output = output
        self.index = -1

    def add_child(self, feature_value, obj):
        self.children[feature_value] = obj


In [31]:
class DTClasy:
    def __init__(self):
        self.__root = None

    def unique(self, Y):
        d = {}
        for i in Y:
            if i not in d:
                d[i] = 1
            else:
                d[i] += 1
        return d


    def entropy(self, Y):
        freq_map = self.unique(Y)
        entropy_ = 0
        total = len(Y)
        for i in freq_map:
            p = freq_map[i] / total
            entropy_ += (-p) * math.log2(p)
        return entropy_

    
    def gain_ratio(self, X, Y, selected_feature):
        info_orig = self.entropy(Y)
        info_f = 0
        split_info = 0
        values = set(X[:, selected_feature])
        df = pd.DataFrame(X)
        df[df.shape[1]] = Y
        initial_size = df.shape[0]
        for i in values:
            df1 = df[df[selected_feature] == i]
            current_size = df1.shape[0]
            info_f += (current_size / initial_size) * self.entropy(df1[df1.shape[1] - 1])
            split_info += (-current_size / initial_size) * math.log2(current_size / initial_size)

        if split_info == 0:
            return math.inf

        info_gain = info_orig - info_f
        gain_ratio = info_gain / split_info
        return gain_ratio
    
    
    def dt(self, X, Y, features, level, classes, max_levels):
        if len(set(Y)) == 1:
            print("Level-->", level)
            output = None
            for i in classes:
                if i in Y:
                    output = i
                    print("Count of", i, "=", len(Y))
                else:
                    print("Count of", i, "=", 0)
            print("Entropy is =  0.0")

            print("Reached leaf Node")
            print()
            return TreeNode(None, output)

        if len(features) == 0 or level >= max_levels:
            print("Level-->", level)
            fmap = self.unique(Y)
            output = None
            max_count = -math.inf
            for i in classes:
                if i not in fmap:
                    print("Count of", i, "=", 0)
                else:
                    if fmap[i] > max_count:
                        output = i
                        max_count = fmap[i]
                    print("Count of", i, "=", fmap[i])

            print("Entropy  is =", self.entropy(Y))

            print("Reached leaf Node")
            print()
            return TreeNode(None, output)

        max_gain = -math.inf
        ff = None
        for f in features:
            current_gain = self.gain_ratio(X, Y, f)

            if current_gain > max_gain:
                max_gain = current_gain
                ff = f

        print("Level-->", level)
        fmap = self.unique(Y)
        output = None
        max_count = -math.inf

        for i in classes:
            if i not in fmap:
                print("Count of", i, "=", 0)
            else:
                if fmap[i] > max_count:
                    output = i
                    max_count = fmap[i]
                print("Count of", i, "=", fmap[i])

        print("Entropy is =", self.entropy(Y))
        print("Splitting on feature  X[", ff, "] with gain ratio ", max_gain, sep="")

        uniqueval = set(X[:, ff])
        df = pd.DataFrame(X)
        df[df.shape[1]] = Y

        cnode = TreeNode(ff, output)

        index = features.index(ff)
        features.remove(ff)
        for i in uniqueval:
            df1 = df[df[ff] == i]
            node = self.dt(df1.iloc[:, 0:df1.shape[1] - 1].values, df1.iloc[:, df1.shape[1] - 1].values,
                           features, level + 1, classes, max_levels)
            cnode.add_child(i, node)

        features.insert(index, ff)

        return cnode
    
    def fit(self, X, Y, max_levels):
        features = [i for i in range(len(X[0]))]
        classes = set(Y)
        level = 0
        self.__root = self.dt(X, Y, features, level, classes, max_levels)
        
    def predictfor(self, data, node):
        if len(node.children) == 0:
            return node.output

        val = data[node.data]
        if val not in node.children:
            return node.output

        return self.predictfor(data, node.children[val])

    def predict(self, X):
        Y = np.array([0 for i in range(len(X))])
        for i in range(len(X)):
            Y[i] = self.predictfor(X[i], self.__root)
        return Y

    def score(self, X, Y):
        Y_pred = self.predict(X)
        count = 0
        for i in range(len(Y_pred)):
            if Y_pred[i] == Y[i]:
                count += 1
        return count / len(Y_pred)

In [32]:
df = df.sample(frac=1)
train_size = int(0.7 * len(df))

train_set = df[:train_size]
test_set = df[train_size:]

X_train = train_set.iloc[:, :-1]
X_test = test_set.iloc[:, :-1]
Y_train = train_set.income_class
Y_test = test_set.income_class


In [33]:
clf1 = DTClasy()

max_levels = 2
clf1.fit(X_train.to_numpy(), Y_train.to_numpy(), max_levels)

Level--> 0
Count of 0 = 23476
Count of 1 = 7572
Entropy is = 0.8014339881310844
Splitting on feature  X[4] with gain ratio 0.08375946931572228
Level--> 1
Count of 0 = 4090
Count of 1 = 457
Entropy is = 0.47059698281038487
Splitting on feature  X[3] with gain ratio 0.030783194543745163
Level--> 2
Count of 0 = 37
Count of 1 = 0
Entropy is =  0.0
Reached leaf Node

Level--> 2
Count of 0 = 264
Count of 1 = 4
Entropy  is = 0.11190990870168403
Reached leaf Node

Level--> 2
Count of 0 = 1709
Count of 1 = 85
Entropy  is = 0.2751620464040846
Reached leaf Node

Level--> 2
Count of 0 = 1392
Count of 1 = 107
Entropy  is = 0.37105597297364173
Reached leaf Node

Level--> 2
Count of 0 = 670
Count of 1 = 241
Entropy  is = 0.8335268802316214
Reached leaf Node

Level--> 2
Count of 0 = 18
Count of 1 = 20
Entropy  is = 0.9980008838722996
Reached leaf Node

Level--> 1
Count of 0 = 19
Count of 1 = 10
Entropy is = 0.9293636260137187
Splitting on feature  X[10] with gain ratio inf
Level--> 2
Count of 0 = 19
C

In [34]:
print("Score :", clf1.score(X_test.to_numpy(), Y_test.to_numpy()))

Score : 0.8128804388667619


In [35]:
num_folds = 5
shuffled = train_set.sample(frac=1)
result = np.array_split(shuffled, num_folds)

In [36]:
maxLevel = [2, 3, 4, 5, 6]
avgacc = []
for k in maxLevel:
    acc = []
    for i in range(len(result)):
        valid = result[i]
        frames = [result[j] for j in range(len(result)) if j != i]
        train = pd.concat(frames)
        X_train = train.iloc[:, :-1]
        Y_train = train.income_class
        X_valid = valid.iloc[:, :-1]
        Y_valid = valid.income_class
        clf1 = DTClasy()
        clf1.fit(X_train.to_numpy(), Y_train.to_numpy(), k)
        acc.append(clf1.score(X_test.to_numpy(), Y_test.to_numpy()))
    avgacc.append(np.mean(acc))


Level--> 0
Count of 0 = 18823
Count of 1 = 6015
Entropy is = 0.7986291058879148
Splitting on feature  X[4] with gain ratio 0.08245465366396898
Level--> 1
Count of 0 = 3306
Count of 1 = 362
Entropy is = 0.46483360302675836
Splitting on feature  X[3] with gain ratio 0.034053276592360175
Level--> 2
Count of 0 = 29
Count of 1 = 0
Entropy is =  0.0
Reached leaf Node

Level--> 2
Count of 0 = 214
Count of 1 = 1
Entropy  is = 0.042732686380876794
Reached leaf Node

Level--> 2
Count of 0 = 1381
Count of 1 = 64
Entropy  is = 0.2616301154639109
Reached leaf Node

Level--> 2
Count of 0 = 1136
Count of 1 = 86
Entropy  is = 0.3673268540562915
Reached leaf Node

Level--> 2
Count of 0 = 535
Count of 1 = 193
Entropy  is = 0.8343597821188995
Reached leaf Node

Level--> 2
Count of 0 = 11
Count of 1 = 18
Entropy  is = 0.9575534837147482
Reached leaf Node

Level--> 1
Count of 0 = 15
Count of 1 = 10
Entropy is = 0.9709505944546686
Splitting on feature  X[10] with gain ratio inf
Level--> 2
Count of 0 = 15
Co

In [37]:
topmaxlevel = maxLevel[np.argmax(avgacc)]
print("max accuracy with max levels value--> " + str(topmaxlevel))

max accuracy with max levels value--> 6


In [38]:
clf1 = DTClasy()
clf1.fit(X_train.to_numpy(), Y_train.to_numpy(), topmaxlevel)

Level--> 0
Count of 0 = 18764
Count of 1 = 6075
Entropy is = 0.8025660279524869
Splitting on feature  X[4] with gain ratio 0.08273686133976021
Level--> 1
Count of 0 = 3242
Count of 1 = 389
Entropy is = 0.49120725401048027
Splitting on feature  X[3] with gain ratio 0.033261642377407676
Level--> 2
Count of 0 = 30
Count of 1 = 0
Entropy is =  0.0
Reached leaf Node

Level--> 2
Count of 0 = 216
Count of 1 = 4
Entropy is = 0.13110652958234503
Splitting on feature  X[10] with gain ratio 0.043064420885726484
Level--> 3
Count of 0 = 0
Count of 1 = 1
Entropy is =  0.0
Reached leaf Node

Level--> 3
Count of 0 = 1
Count of 1 = 0
Entropy is =  0.0
Reached leaf Node

Level--> 3
Count of 0 = 2
Count of 1 = 0
Entropy is =  0.0
Reached leaf Node

Level--> 3
Count of 0 = 4
Count of 1 = 0
Entropy is =  0.0
Reached leaf Node

Level--> 3
Count of 0 = 2
Count of 1 = 0
Entropy is =  0.0
Reached leaf Node

Level--> 3
Count of 0 = 199
Count of 1 = 3
Entropy is = 0.11146303230451957
Splitting on feature  X[9] w

In [39]:
print("Test set with max level value-->" + str(topmaxlevel))
print('Best Accuracy : {:^0.5f}'.format(clf1.score(X_test.to_numpy(), Y_test.to_numpy()), 2))

Test set with max level value-->6
Best Accuracy : 0.81837
